In [1]:
import itertools
import numpy as np
import os
import seaborn as sns
from tqdm import tqdm
from dataclasses import asdict, dataclass, field
import vsketch
import shapely.geometry as sg
from shapely.geometry import box, MultiLineString, Point, MultiPoint, Polygon, MultiPolygon, LineString
import shapely.affinity as sa
import shapely.ops as so
import matplotlib.pyplot as plt
import pandas as pd

import vpype_cli
from typing import List, Generic
from genpen import genpen as gp, utils as utils
from scipy import stats as ss
import geopandas
from shapely.errors import TopologicalError
import functools
%load_ext autoreload
%autoreload 2
import vpype
from skimage import io
from pathlib import Path

import bezier

from sklearn.preprocessing import minmax_scale
from skimage import feature
from genpen.utils import Paper

from scipy import spatial, stats
from scipy.ndimage import gaussian_filter
from scipy.integrate import odeint
from scipy.signal import decimate

In [2]:
from scipy.io.wavfile import read


In [55]:
# make page
paper_size = '17x23.5 inches'
border:float=35
paper = Paper(paper_size)

drawbox = paper.get_drawbox(border)
layers = []

In [56]:
hz, a = read("/mnt/c/data/side/craigie.wav")
a = np.array(a,dtype=float)
df = pd.DataFrame(a)
df.index = pd.to_timedelta(df.index / hz, unit='s')

df = df.rename(columns={0:'L', 1:'R'})
dfrs = df.resample('1ms').mean()

start = '170s'
end = '260s'
clip = dfrs.loc[start:end, :]

In [4]:
baseline_spiral = np.linspace(0, 1, n_samples) ** 0.5

In [ ]:
angle_max = np.pi*40
signal_weight = 0.008
n_samples = len(signal)
baseline_spiral = np.linspace(0, 1, n_samples) ** 0.5
angles = np.linspace(0, angle_max ** 2, n_samples) ** 0.5

radii = baseline_spiral + signal * signal_weight
xs = np.cos(thetas) * radii
ys = np.sin(thetas) * radii

In [57]:


signal = clip['L'].values
signal /= signal.std()
spiral = np.linspace(0, 1, len(signal)) ** 0.5
thetas = np.linspace(0, (np.pi*40) ** 2 , len(signal)) ** 0.5
scale = 0.008
rs = spiral + signal * scale
xs = np.cos(thetas) * rs
ys = np.sin(thetas) * rs
line = LineString(np.flipud(np.stack([xs, ys]).T))
layer = gp.make_like(line, drawbox)
layers.append(layer)

signal = clip['R'].values
signal /= signal.std()
spiral = np.linspace(0, 1, len(signal)) ** 0.5
thetas = np.linspace(0, (np.pi*40) ** 2 , len(signal)) ** 0.5
scale = 0.008
rs = spiral + signal * scale
xs = np.cos(thetas) * rs
ys = np.sin(thetas) * rs
line = LineString(np.flipud(np.stack([xs, ys]).T))
layer = gp.make_like(line, drawbox)
layers.append(layer)

In [58]:
hz, a = read("/mnt/c/data/side/craigie.wav")
a = np.array(a,dtype=float)
df = pd.DataFrame(a)
df.index = pd.to_timedelta(df.index / hz, unit='s')

df = df.rename(columns={0:'L', 1:'R'})
dfrs = df

start = '170s'
end = '260s'
clip = dfrs.loc[start:end, :]
short_clip = dfrs.loc['184s':'195s', :]

# signal = clip['L'].values
# signal = decimate(signal, 5)
# signal = decimate(signal, 5)
# signal /= signal.std()
# spiral = np.linspace(0, 1, len(signal)) ** 0.5
# thetas = np.linspace(0, (np.pi*40) ** 2 , len(signal)) ** 0.5
# scale = 0.008
# rs = spiral + signal * scale
# xs = np.cos(thetas) * rs
# ys = np.sin(thetas) * rs
# line = LineString(np.flipud(np.stack([xs, ys]).T))
# layer = gp.make_like(line, drawbox)
# layers.append(layer)

signal = clip['R'].values
signal = decimate(signal, 7)
signal = decimate(signal, 7)
signal /= signal.std()
spiral = np.linspace(0, 1, len(signal)) ** 0.5
thetas = np.linspace(0, (np.pi*40) ** 2 , len(signal)) ** 0.5
scale = 0.008
rs = spiral + signal * scale
xs = np.cos(thetas) * rs
ys = np.sin(thetas) * rs
line = LineString(np.flipud(np.stack([xs, ys]).T))
layer = gp.make_like(line, drawbox)
layers.append(layer)

In [ ]:
theta_max = np.pi * 40

In [ ]:
n_samples = len(signal)
spiral = np.linspace(0, 1, n_samples) ** 0.5
thetas = np.linspace(0, theta_max ** 2 , n_samples) ** 0.5
signal_weight = 0.008
rs = spiral + signal * signal_weight
xs = np.cos(thetas) * rs
ys = np.sin(thetas) * rs

In [59]:
[len(layer.coords) for layer in layers]

[91000, 91000, 81900]

In [60]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.3mm')

for i, layer in enumerate(layers):
    sk.stroke(i+1)
    sk.geometry(layer)

sk.penWidth('0.3')
sk.vpype('linesimplify')
sk.vpype('linesimplify')
# sk.vpype('linesimplify')
# sk.vpype('linesimplify')

sk.display(color_mode='layer')

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2021-01-29T11:40:47.407396 
 
 
 
 
 
 <polyline points="1491.6424,1135.8356 1493.1874,1135.3626 1497.8554,1134.8831 1490.0905,1134.4229 1495.2626,1133.9377 1497.0086,1133.4572 1491.6229,1133.0039 1493.0199,1132.5251 1498.5149,1132.0218 1490.7583,1131.5933 1496.7624,1131.0805 1496.4815,1130.607 1488.9799,1130.1938 1496.1059,1129.6597 1495.9398,1129.1862 1490.8148,1128.7643 1496.2834,1128.2324 1498.9346,1127.726 1486.6959,1127.401 1497.3909,1126.792 1496.2523,1126.3317 1490.3506,1125.9419 1495.9717,1125.3853 1494.9021,1124.9272 1493.1088,1124.4825 1496.3628,1123.9532 1496.435,1123.4764 1490.522,1123.1112 1496.2285,1122.5294 1493.7239,1122.1042 1490.8054,1121.691 1497.137,1121.0838 1493.448,1120.6893 1489.883,1120.297 1499.7165,1119.595 1493.3097,1119.272 1493.446,1118.7951 1496.3681,1118.2468 1493.4598,1117.8475 1490.0298,1117.4663 1496.9565,1116.8036 1494.397,1116.4 1492.1848,1115.9898 1497.7449,1115.3518 1490.1742,1115.1052 1492.3018,1114.5675 1498.977,1113.8824 1489.1524,1113.7238 1493.3251,1113.1145 1497.3406,1112.5048 1491.1798,1112.2411 1492.8738,1111.709 1497.1719,1111.0811 1492.268,1110.7841 1491.3395,1110.3456 1499.2555,1109.5722 1488.9141,1109.4943 1492.5513,1108.8801 1499.6987,1108.1202 1488.3521,1108.1043 1494.1499,1107.3933 1498.3293,1106.7425 1490.0265,1106.6206 1494.1072,1105.971 1495.8339,1105.4199 1490.4633,1105.1852 1492.808,1104.606 1498.0431,1103.8897 1489.2224,1103.8266 1494.5196,1103.1025 1497.6446,1102.4761 1487.0888,1102.5166 1495.7442,1101.6158 1495.8945,1101.132 1488.5012,1101.0339 1496.2716,1100.1598 1495.563,1099.7204 1488.0045,1099.6465 1494.7161,1098.8136 1496.3054,1098.2511 1487.4684,1098.2631 1494.4814,1097.3996 1496.2009,1096.8265 1488.9485,1096.7658 1496.5904,1095.8501 1492.6736,1095.6031 1488.8382,1095.3566 1494.4393,1094.5477 1494.5164,1094.0672 1489.807,1093.8811 1494.6418,1093.1074 1493.4293,1092.7076 1489.2939,1092.4954 1494.8968,1091.6625 1494.0099,1091.2438 1488.7659,1091.1125 1493.8488,1090.3027 1494.956,1089.7526 1489.3339,1089.657 1494.2494,1088.8476 1493.1333,1088.4485 1489.2932,1088.2413 1495.0823,1087.3599 1492.0901,1087.0961 1488.1774,1086.9027 1497.0873,1085.7831 1491.8966,1085.6853 1487.9437,1085.503 1496.49,1084.392 1493.1158,1084.1682 1488.3342,1084.0562 1494.1084,1083.14 1492.3712,1082.7979 1488.7475,1082.6056 1496.0278,1081.5581 1490.8234,1081.494 1487.1947,1081.3107 1495.8697,1080.1359 1491.1342,1080.0444 1490.8033,1079.5965 1496.1468,1078.6777 1488.1173,1078.8717 1488.7305,1078.3467 1495.409,1077.3043 1489.2535,1077.3545 1491.0396,1076.7257 1495.1634,1075.8905 1489.1405,1075.9418 1489.321,1075.4516 1493.3062,1074.6211 1490.2388,1074.4201 1490.6455,1073.908 1494.2314,1073.1046 1487.8392,1073.2154 1489.4803,1072.5894 1494.593,1071.6364 1488.3124,1071.7496 1490.1277,1071.1031 1495.014,1070.1603 1488.6564,1070.2936 1489.1232,1069.7737 1493.1914,1068.9012 1487.7729,1068.9564 1489.9627,1068.2651 1494.4311,1067.3434 1489.0534,1067.4048 1489.3874,1066.8957 1493.3647,1066.0148 1487.242,1066.1644 1489.2588,1065.4818 1495.4357,1064.3638 1487.0917,1064.7571 1488.7799,1064.1048 1492.3833,1063.247 1486.1683,1063.4324 1490.1246,1062.5332 1494.0448,1061.6323 1488.7468,1061.7295 1489.7056,1061.1485 1491.4365,1060.4809 1484.743,1060.7457 1489.5929,1059.7307 1491.1801,1059.0755 1486.7718,1059.0959 1492.7576,1057.9398 1493.0704,1057.4247 1484.3944,1057.9443 1488.6162,1056.9815 1490.2407,1056.3155 1485.2631,1056.4213 1490.747,1055.2999 1492.247,1054.6435 1486.7703,1054.8178 1489.753,1053.9839 1488.8849,1053.6108 1485.5251,1053.5415 1491.1835,1052.375 1489.6432,1052.0851 1485.8975,1052.0698 1490.3758,1051.0376 1488.8401,1050.7507 1484.7429,1050.7878 1492.178,1049.3729 1488.1363,1049.4062 1485.2222,1049.301 1492.2201,1047.9261 1488.1784,1047.9676 1485.8485,1047.7923 1490.5332,1046.7041 1485.7447,1046.8531 1485.0357,1046.4702 1491.214,1045.1741 1487.7042,1045.1619 1486.2479,1044.8791 1490.0285,1043.8921 1486.4338,1043.8994 1485.26

In [61]:
sk.save('/mnt/c/code/side/plotter_images/oned_outputs/254_use_sound.svg')